<a href="https://colab.research.google.com/github/Nikitha1418/INFO5731/blob/master/INFO5731_Assignment_Two.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **INFO5731 Assignment Two**

In this assignment, you will try to gather text data from open data source via web scraping or API. After that you need to clean the text data and syntactic analysis of the data.

# **Question 1**

(40 points). Write a python program to collect text data from **either of the following sources** and save the data into a **csv file**:

(1) Collect all the customer reviews of the product [2019 Dell labtop](https://www.amazon.com/Dell-Inspiron-5000-5570-Laptop/dp/B07N49F51N/ref=sr_1_11?crid=1IJ7UWF2F4GHH&keywords=dell%2Bxps%2B15&qid=1580173569&sprefix=dell%2Caps%2C181&sr=8-11&th=1) on amazon.

(2) Collect the top 100 User Reviews of the film [Joker](https://www.imdb.com/title/tt7286456/reviews?ref_=tt_urv) from IMDB.

(3) Collect the abstracts of the top 100 research papers by using the query [natural language processing](https://citeseerx.ist.psu.edu/search?q=natural+language+processing&submit.x=0&submit.y=0&sort=rlv&t=doc) from CiteSeerX.

(4) Collect the top 100 tweets by using hashtag ["#CovidVaccine"](https://twitter.com/hashtag/CovidVaccine) from Twitter. 


In [104]:
!apt-get update 
!apt install chromium-chromedriver
!cp /usr/lib/chromium-browser/chromedriver /usr/bin
!pip install selenium

Hit:1 http://archive.ubuntu.com/ubuntu bionic InRelease
Hit:2 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease
Get:3 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Ign:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Get:5 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Ign:6 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:7 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease
Get:8 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release [697 B]
Hit:9 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Get:10 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release.gpg [836 B]
Get:11 http://archive.ubuntu.com/ubuntu bionic-backports InRelease [74.6 kB]
Hit:12 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu bionic

In [105]:
from selenium import webdriver
options = webdriver.ChromeOptions()
options.add_argument('-headless')
options.add_argument('-no-sandbox')
options.add_argument('-disable-dev-shm-usage')

In [53]:
from selenium import webdriver
import pandas as pd
import time

driver = webdriver.Chrome('chromedriver',options=options)
url = "https://www.amazon.com/Dell-Inspiron-5000-5570-Laptop/product-reviews/B07N49F51N/ref=cm_cr_dp_d_show_all_btm?ie=UTF8&reviewerType=all_reviews"
comments = []
driver.get(url)
time.sleep(4)
page = BeautifulSoup(driver.page_source,'lxml')
all_divs = page.findAll('div')
for ele in all_divs:
  if(ele.get('id')):
    if('-review-card' in ele.get('id')):
      get_span_data = ele.find('span',{'data-hook':'review-body'}).text
      comments.append(get_span_data.replace('\n',''))
next_button = driver.find_element_by_class_name("a-last")
while(next_button):
  driver.find_element_by_class_name("a-last").click()
  time.sleep(4)
  page = BeautifulSoup(driver.page_source,'lxml')
  all_divs = page.findAll('div')
  for ele in all_divs:
    if(ele.get('id')):
      if('-review-card' in ele.get('id')):
        get_span_data = ele.find('span',{'data-hook':'review-body'}).text
        comments.append(get_span_data.replace('\n',''))
  page = BeautifulSoup(driver.page_source,'lxml')
  next_button = page.find('li',{'class':'a-last'})
  if('a-disabled' in next_button.get('class')):
      break
input_data = pd.DataFrame({'Reviews': comments})
input_data

Reviews
0      I bought this computer because I was looking...
1      I am a software developer and have been usin...
2      I bought this laptop for personal home use. ...
3      We purchased this laptop for my college-boun...
4      It came poorly packed and not usable as the ...
..                                                 ...
105    Warning: Avoid all Dell products in the even...
106    The screen quality is very good, especially ...
107    The DC adapter plugin, is not a tight fit an...
108    This is my second Dell laptop. The first one...
109    overall this laptop is ok. I don't love it. ...

[110 rows x 1 columns]

In [106]:
import nltk
nltk.download()

NLTK Downloader
---------------------------------------------------------------------------
    d) Download   l) List    u) Update   c) Config   h) Help   q) Quit
---------------------------------------------------------------------------
Downloader> d

Download which package (l=list; x=cancel)?
  Identifier> all
       | 
       | Downloading package abc to /root/nltk_data...
       |   Package abc is already up-to-date!
       | Downloading package alpino to /root/nltk_data...
       |   Package alpino is already up-to-date!
       | Downloading package biocreative_ppi to /root/nltk_data...
       |   Package biocreative_ppi is already up-to-date!
       | Downloading package brown to /root/nltk_data...
       |   Package brown is already up-to-date!
       | Downloading package brown_tei to /root/nltk_data...
       |   Package brown_tei is already up-to-date!
       | Downloading package cess_cat to /root/nltk_data...
       |   Package cess_cat is already up-to-date!
       | Down

True

# **Question 2**

(30 points). Write a python program to **clean the text data** you collected above and save the data in a new column in the csv file. The data cleaning steps include:

(1) Remove noise, such as special characters and punctuations.

(2) Remove numbers.

(3) Remove stopwords by using the [stopwords list](https://gist.github.com/sebleier/554280).

(4) Lowercase all texts

(5) Stemming. 

(6) Lemmatization.

**Data Cleaning**

In [107]:
import re
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from textblob import Word
import nltk

In [108]:
def special_characters_count(given_input):
  number_of_special_characters = 0
  for i in range(len(given_input)):
    if not((given_input[i].isalpha()) and (given_input[i].isdigit())):
        number_of_special_characters = number_of_special_characters + 1
  return number_of_special_characters

In [109]:
#Removal of special characters:

input_data['Removal of special characters'] = input_data['Reviews'].apply(lambda x: ''.join(re.sub(r"[^a-zA-Z0-9]+", ' ', charctr) for charctr in x ))

#Removal of punctuations :

input_data['Punctuation'] = input_data['Reviews'].str.replace('[^\w\s]','')

#Removal of numbers:

input_data['Removal of numbers'] = input_data['Reviews'].str.replace('\d+', '')

#Lower case all texts:

input_data['Lower Case words'] = input_data['Reviews'].apply(lambda x: " ".join(x.lower() for x in x.split()))

#Removing stopwords by using stopwordslist

stop = stopwords.words('english')
input_data['removed stopwords'] = input_data['Reviews'].apply(lambda x: " ".join(x for x in x.split() if x not in stop))

#Stemming Data

st = PorterStemmer()
input_data['Stemming'] = input_data['Reviews'].apply(lambda x: " ".join([st.stem(word) for word in x]))

#Lemmatization

nltk.download('wordnet')
input_data['Lemmatization'] = input_data['Stemming'].apply(lambda x: " ".join([Word(word).lemmatize() for word in x.split()]))

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [110]:
#Saving the CleanedData to CSV

input_data.to_csv('output.csv',index=False)

# **Question 3**

(30 points). Write a python program to conduct **syntax and structure analysis** of the clean text you just saved above. The syntax and structure analysis includes: 

(1) Parts of Speech (POS) Tagging: Tag Parts of Speech of each word in the text, and calculate the total number of N(oun), V(erb), Adj(ective), Adv(erb), respectively.

(2) Constituency Parsing and Dependency Parsing: print out the constituency parsing trees and dependency parsing trees of all the sentences. Using one sentence as an example to explain your understanding about the constituency parsing tree and dependency parsing tree.

(3) Named Entity Recognition: Extract all the entities such as person names, organizations, locations, product names, and date from the clean texts, calculate the count of each entity.

In [111]:
from nltk import word_tokenize
PartsOfSpeech = []
for i in input_data['Lower Case words'].tolist():
  tokens = word_tokenize(i)
  PartsOfSpeech.append(nltk.pos_tag(tokens))
print(PartsOfSpeech)

[[('i', 'NN'), ('bought', 'VBD'), ('this', 'DT'), ('computer', 'NN'), ('because', 'IN'), ('i', 'NN'), ('was', 'VBD'), ('looking', 'VBG'), ('for', 'IN'), ('a', 'DT'), ('computer', 'NN'), ('for', 'IN'), ('my', 'PRP$'), ('wife', 'NN'), ('that', 'WDT'), ('had', 'VBD'), (':', ':'), ('a', 'DT'), ('ssd', 'NN'), (',', ','), ('at', 'IN'), ('least', 'JJS'), ('16gb', 'CD'), ('of', 'IN'), ('ram', 'NN'), ('and', 'CC'), ('at', 'IN'), ('least', 'JJS'), ('a', 'DT'), ('i5', 'NN'), ('processor', 'NN'), ('.', '.'), ('also', 'RB'), ('my', 'PRP$'), ('wife', 'NN'), ('feels', 'NNS'), ('more', 'RBR'), ('comfortable', 'JJ'), ('working', 'VBG'), ('on', 'IN'), ('windows.this', 'JJ'), ('one', 'CD'), ('was', 'VBD'), ('a', 'DT'), ('good', 'JJ'), ('balance', 'NN'), ('between', 'IN'), ('price', 'NN'), ('and', 'CC'), ('specs', 'NN'), ('.', '.'), ('it', 'PRP'), ('looks', 'VBZ'), ('a', 'DT'), ('lot', 'NN'), ('like', 'IN'), ('a', 'DT'), ('macbook', 'NN'), ('pro', 'NN'), (',', ','), ('but', 'CC'), ('it', 'PRP'), ('feels',

In [112]:
from collections import Counter
CountOfPartsOfSpeech = []
for j in PartsOfSpeech:
  pos_count = Counter(tag for word, tag in j)
  CountOfPartsOfSpeech.append(pos_count)
print(CountOfPartsOfSpeech)

[Counter({'NN': 29, 'DT': 20, 'IN': 20, 'JJ': 13, 'VBD': 10, 'RB': 8, '.': 6, 'VBZ': 6, 'VBG': 5, 'PRP': 5, 'WDT': 4, ',': 4, 'CD': 4, 'CC': 4, 'NNS': 3, 'VBP': 3, 'PRP$': 2, 'JJS': 2, 'RBR': 2, ':': 1, 'VB': 1, 'PDT': 1, 'TO': 1}), Counter({'NN': 45, 'DT': 23, 'IN': 18, 'JJ': 9, 'RB': 9, 'CC': 8, '.': 8, 'VBP': 7, 'VBG': 6, 'NNS': 6, 'VBD': 6, ',': 6, 'VBZ': 5, 'VBN': 3, 'VB': 3, 'CD': 2, 'JJR': 2, 'MD': 2, 'PRP': 1, 'PRP$': 1, 'PDT': 1, 'JJS': 1}), Counter({'NN': 22, 'JJ': 12, 'DT': 9, 'IN': 8, '.': 7, 'RB': 6, 'VB': 6, 'CC': 5, 'VBZ': 5, 'VBD': 3, 'VBG': 3, 'TO': 3, 'VBP': 2, ',': 2, 'NNS': 1, 'PRP': 1, 'PDT': 1, 'PRP$': 1, 'CD': 1, 'WDT': 1, 'WP': 1, 'VBN': 1}), Counter({'NN': 9, 'DT': 6, 'JJ': 4, 'CC': 4, 'RB': 4, 'PRP': 3, 'IN': 3, '.': 3, 'VBP': 3, 'VBD': 2, ',': 2, 'CD': 2, 'VBZ': 2, 'PRP$': 1, 'WDT': 1, 'VBN': 1, 'WRB': 1, 'MD': 1, 'VB': 1}), Counter({'NN': 12, 'IN': 8, 'RB': 6, 'JJ': 6, 'DT': 6, 'VBN': 5, 'NNS': 5, 'VBD': 4, '.': 4, 'CC': 3, 'PRP': 2, 'VB': 2, ',': 2, 'CD': 2

In [113]:
import benepar
import spacy
from benepar.spacy_plugin import BeneparComponent
nlp = spacy.load('en')
nlp.add_pipe(BeneparComponent("benepar_en2"))
for i in input_data['Lower Case words'].tolist():
  print(list(nlp(i).sents)[0]._.parse_string)

(S (NP (PRP i)) (VP (VBD bought) (NP (DT this) (NN computer)) (SBAR (IN because) (S (NP (PRP i)) (VP (VBD was) (VP (VBG looking) (PP (IN for) (NP (NP (DT a) (NN computer)) (PP (IN for) (NP (PRP$ my) (NN wife))) (SBAR (WHNP (WDT that)) (S (VP (VBD had) (: :) (NP (NP (DT a) (NNP ssd)) (, ,) (NP (NP (QP (IN at) (JJS least) (CD 16)) (NNS gb)) (PP (IN of) (NP (NN ram)))) (CC and) (NP (ADVP (IN at) (JJS least)) (DT a) (CD i5) (NN processor))))))))))))) (. .))
(S (NP (PRP i)) (VP (VP (VBP am) (NP (DT a) (NN software) (NN developer))) (CC and) (VP (VBP have) (VP (VBN been) (VP (VBG using) (NP (DT some) (ADJP (NN memory) (JJ intensive)) (NNS programs))))) (CC and) (VP (VBD needed) (NP (DT an) (NN upgrade)))) (. .))
(S (NP (PRP i)) (VP (VBD bought) (NP (DT this) (NN laptop)) (PP (IN for) (NP (JJ personal) (NN home) (NN use)))) (. .))
(S (NP (PRP we)) (VP (VBD purchased) (NP (DT this) (NN laptop)) (PP (IN for) (NP (PRP$ my) (NN college) (: -) (JJ bound) (NN engineering) (NN student)))) (. .))
(S 

In [114]:
from spacy import displacy
for i in input_data['Lower Case words'].tolist():
  doc = nlp(i)
  displacy.render(doc, options={'distance': 120}, style = 'dep', jupyter = True)

In [115]:
for i in input_data['Lower Case words'].tolist():
  doc = nlp(i)
  for j in doc.ents:
    print([(j.text, j.label_)])

[('at least 16', 'CARDINAL')]
[('1tb', 'QUANTITY')]
[('second', 'ORDINAL')]
[('about 12 seconds', 'TIME')]
[('about 10', 'CARDINAL')]
[('a little less than half', 'TIME')]
[('a ton', 'QUANTITY')]
[('touchscreen', 'DATE')]
[('microsoft', 'ORG')]
[('many hours', 'TIME')]
[('one', 'CARDINAL')]
[('1', 'CARDINAL')]
[('ten minutes', 'TIME')]
[('scan', 'PERSON')]
[('9 days ago', 'DATE')]
[('700.00', 'MONEY')]
[('4', 'CARDINAL')]
[('two hours', 'TIME')]
[('m.2', 'PRODUCT')]
[('1 tb', 'QUANTITY')]
[('3 weeks', 'DATE')]
[('amazon', 'ORG')]
[('one month', 'DATE')]
[('just a few hours', 'TIME')]
[('amazon', 'ORG')]
[('amazon', 'ORG')]
[('7 year old', 'DATE')]
[('better days', 'DATE')]
[('months', 'DATE')]
[('3 00 to $400', 'MONEY')]
[('about a month and a half', 'DATE')]
[('seconds', 'TIME')]
[('amazon', 'ORG')]
[('trackpad', 'PERSON')]
[('touchscreen', 'ORG')]
[('buzzy', 'PERSON')]
[('30', 'CARDINAL')]
[('3', 'CARDINAL')]
[('about 15 minutes', 'TIME')]
[('4 minutes 38 seconds', 'TIME')]
[('about 

**Write your explanations of the constituency parsing tree and dependency parsing tree here (Question 3-2):** 

In [ ]:
'''
Write your explanations of the constituency parsing tree and dependency parsing tree here

Constituency parsing represents syntactic structure of a sentence according to grammar.
As a part of this parsing, we divide a sentence into sub-texts, also called constituents.
Using specific rules, we generate valid sentences. 

Dependency parsing represents grammatical structure of a sentence.
It also explains grammatical relation between words in the sentence.

'''

'\nWrite your explanations of the constituency parsing tree and dependency parsing tree here\n\n\n\n'